# Добавление контекста в промпт большой языковой модели, для реализации чат-бота

Задачу использования в чат боте языковой моделью контекста (новых данных) без дообучения можно решить так:
1. Собрать датасет новых текстовых данных. Разбить его на части. Например на абзацы. Для каждого абзаца создать с помощью простой языковой модели (например BERT, LABSE) векторные представления.
2. Вычислить векторное представление текстового запроса пользователя той же моделью. Отобрать топ K похожих текстов сравнивая вектор запроса пользователя с векторами известных абзацев. Это будет контекстом запроса.
3. Составит промпт из К отобранных абзацев датасета и запроса пользователя. Отправить промпт в языковую модель обученную быть чатом, например LLama3.

Отбор похожих текстов нужен для того, чтобы уместить контекст в промпт языковой модели чат-бота (например LLama3). Т.к. обычно датасет дополнительной информации большой и весь не войдёт в промпт.

Это называется Retrieval-Augmented Generation (RAG) или Context Application?

Примерная схема решения:

<img src="https://habrastorage.org/r/w1560/getpro/habr/upload_files/a65/c81/973/a65c8197331c24fea7b7b4a5a0985795.png">

**Запуск сервера с моделью**

Коротко о OLLAMA: https://github.com/ivtipm/ML/blob/main/tools.md

```bash
ollama run gemma:7b
```

In [1]:
# requirements.txt
#%pip install sentence-transformers langchain-community langchain  faiss-cpu faiss-gpu ollama pandas
#%pip install pandas
%pip install langchain
%pip install langchain-community
%pip install sentence_transformers
%pip install faiss-cpu
%pip install ollama

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


**LangChain**

Это пакет для взаимодействия с языковыми моделями разного рода (чат-боты, модели для генерации текста, модели выдающие эмбеддинги и т.п.).

Предоставляет высокоуровневые типы данных и функции для вышеописанных задач.




In [2]:
import pandas as pd
from langchain.document_loaders import DataFrameLoader                  # отдельный тип для хранения датафреймов
# будет разбивать тексты на части, чтобы делать их них эмбеддинги
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [10]:
# загрузка датасета, из которого будет использоваться информация для дополнения промпта
import json

def load_dataset( filename:str ):
    """Загружает датасет из вопросов и ответов.
    Формат файла:
    Вопрос? <одна строка>
    Ответ,
    ответ может занимает несколько абзацев или строк
    @return: DataFrame(columns=['Q', 'A'])"""

    Q = []      # вопросы
    A = []      # ответы
    print('Начало обработки файла')
    # загрузка вопросов и ответов из файла
    with open( filename ) as f_in:
        json_dict = json.load(f_in)
        print(type(json_dict))
    print('Конец обработки файла')
    data = pd.DataFrame( {"Q":Q, "A":A})
    return data

data = load_dataset("dataset.json")

Начало обработки файла
<class 'dict'>
Конец обработки файла


In [6]:
data = load_dataset("dataset.json")

loader = DataFrameLoader(data, page_content_column='Q')         # зададим ключ для поиска по текстам, это колонка с вопросом
documents = loader.load()                                       # обёртка над датафреймом, отсюда будем брать контекст

data
# loader

{'data': [{'id': '3e75f57f-3f6f-4eaf-ae5d-ec6586d201f1', 'title': 'Как посмотреть лимиты счета?', 'url': 'https://www.tinkoff.ru/business/help/business-payout/jump/about/summary/?card=q1', 'source': 'web', 'business_line_id': 'business', 'direction': 'business-payout', 'product': 'jump', 'type': 'card', 'description': 'Вы можете посмотреть лимиты по счету на месяц, по карте на месяц и на разовую выплату. Для этого: Откройте раздел «Сводка». В разделе «Счета» найдите нужное вам юридическое лицо и нажмите на него. В открывшемся окне будут представлены все расчетные счета, к которым есть доступ с этого юридического лица. Найдите нужный вам счет.', 'parent_title': 'Сводка', 'parent_url': 'https://www.tinkoff.ru/business/help/business-payout/jump/about/summary/'}, {'id': '1667e934-bf2a-421c-b565-df322e9a6921', 'title': 'Как посмотреть выплаты за определенный период?', 'url': 'https://www.tinkoff.ru/business/help/business-payout/jump/about/summary/?card=q2', 'source': 'web', 'business_line_i

Empty DataFrame
Columns: [Q, A]
Index: []

In [54]:
# класс-обёртка для создания эмбеддингов текстов
from langchain_community.embeddings import HuggingFaceEmbeddings

# сравнительно простая (и быстрая) модель, выдаёт эмбеддинги () для текстов

model_name = "cointegrated/LaBSE-en-ru"
model_kwargs = {'device': 'cpu'}
encode_kwargs = {'normalize_embeddings': False}
embeddings_maker = HuggingFaceEmbeddings(
    model_name=model_name,
    model_kwargs=model_kwargs,
    encode_kwargs=encode_kwargs
)

c:\Users\ramen\AppData\Local\Programs\Python\Python311\Lib\site-packages\huggingface_hub\file_download.py:157: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\ramen\.cache\huggingface\hub\models--cointegrated--LaBSE-en-ru. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to see activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


In [55]:
# максимальная длина (в токенах) входной последовательности
embeddings_maker.client.max_seq_length                  # 384

512

In [56]:
# размерность эмбеддинга
embeddings_maker.client.get_sentence_embedding_dimension()

768

In [57]:
# нейросеть выдающая эмбеддинги текстов
# embeddings_maker.client

In [58]:
# объект, который будет разбивать тексты из датасета на блоки, если вдруг они будут слишком большими для модели выдающий эмбеддинги
text_splitter = RecursiveCharacterTextSplitter(chunk_size = embeddings_maker.client.max_seq_length, chunk_overlap=0)
# text_splitter = RecursiveCharacterTextSplitter(chunk_size = 50, chunk_overlap=0)        # для примера
# chunk_size - это размер блока в токенах, будет разбивать на части только ключ (здесь, это вопрос)

# получим блоки. Блок = (вопрос (ключ), ответ);
# Вопрос может быть не полным, если не поместится в chunk_size. Тогда создаётся новый блок, с остатком вопроса, но с таким же ответом.
texts = text_splitter.split_documents(documents)
len(texts)          # при максимальном размере вопроса в токенах 384, разбивать вопросы на части не пришлось.
# texts

71

In [61]:
# класс для хранения данных как в векторной БД?. Используется для быстрого поиска подходящего контекста по запросу
from langchain.vectorstores import FAISS

# создаем хранилище
db = FAISS.from_documents(texts, embeddings_maker)
db.as_retriever()           # ???ы

# пример использования:
db.similarity_search_with_score('Как участвовать на нескольких хакатонах?', k = 5 )
# поданный запрос переводится в эмбеддинг, для него выдаётся топ K самых похожих частей датасета (вопрос, ответ, расстояние)

[(Document(page_content='Могу ли я участвовать в нескольких хакатонах?', metadata={'A': 'Согласно Положению о проекте вы имеете право участвовать в нескольких хакатонах. Однако в случае занятия 1, 2 или 3 места на одном из окружных хакатонов в 2024 году, вы не сможете принять участие в других окружных хакатонах. Тем не менее вы по-прежнему сможете испытать свои силы во всероссийском и международном хакатонах.'}),
  0.28495383),
 (Document(page_content='Как мне принять участие/подать заявку на участие в окружном хакатоне?', metadata={'A': '1. На сайте проекта https://hacks-ai.ru/ в таймлайне на главной странице выбрать конкретный хакатон (по названию федерального округа), перейти на интересующее мероприятие, после чего нажать кнопку «Зарегистрироваться».  2. Заполнить анкету со всеми необходимыми полями в личном кабинете, обязательные поля помечены символом «*» Важно! Заполняйте свои данные на русском языке без специальных символов и смайлов. Заполняйте поля «Фамилия» и «Имя» только нас

In [62]:
import ollama

# request = 'Мне 10 лет. Я могу участвовать в хакатоне?'
# request = 'Мне 100 лет. Я могу участвовать в хакатоне?'
# request = 'Сколько участников должно быть в команде?'
request = 'Как участвовать на нескольких хакатонах?'

context = db.similarity_search_with_score(request, k = 5 )
context = " ".join([text[0].metadata['A'] for text in context])
print(context)

response = ollama.chat(model='dimweb/ilyagusev-saiga_llama3_8b:Q6_K', messages=[
  {
    'role': 'user',
    'content': f'Дай развёрнутый и как можно более точный ответ. Для ответа используй дополнительную информацию.\nВопрос: {request}.\n Дополнительная информация: {context}',}],
    stream = True
)
# print(response['message']['content'])

for chunk in response:
  print(chunk['message']['content'], end='', flush=True)

Согласно Положению о проекте вы имеете право участвовать в нескольких хакатонах. Однако в случае занятия 1, 2 или 3 места на одном из окружных хакатонов в 2024 году, вы не сможете принять участие в других окружных хакатонах. Тем не менее вы по-прежнему сможете испытать свои силы во всероссийском и международном хакатонах. 1. На сайте проекта https://hacks-ai.ru/ в таймлайне на главной странице выбрать конкретный хакатон (по названию федерального округа), перейти на интересующее мероприятие, после чего нажать кнопку «Зарегистрироваться».  2. Заполнить анкету со всеми необходимыми полями в личном кабинете, обязательные поля помечены символом «*» Важно! Заполняйте свои данные на русском языке без специальных символов и смайлов. Заполняйте поля «Фамилия» и «Имя» только настоящими данными, как указано в паспорте.  3. Подтвердить регистрацию на сайте мероприятия переходом по ссылке в письме, отправленном на адрес электронной почты, указанный при регистрации.  4. Сформировать собственную кома